# Nested merging data analysis
This notebook allows for run-accumulated merging of LD91 data. Beginning with run 95, we add additional runs with every additional merging job, until all runs from 95 to 114 are merged in the final data-set. The idea is to examine the change in the resulting metrics (e.g $CC_{1/2}$, and anomalous peak height), and show that with more frames the metrics improve. 

We begin by ensuring the cctbx environment is loaded and that we are using the correct python from our local Anaconda environment. 

In [1]:
!which libtbx.python

/net/dials/raid1/mlxd/InDev/feb_sprint/build/bin/libtbx.python


To enable MPI for use with mpi4py, we must have be running an ipyparallel cluster in the background of our server. If the ipycluster environment has not yet been installed, we can use conda
```bash
conda install ipycluster
```

For this notebook on dials, we can run the following commands:

```
libtbx.ipython profile create --parallel --profile=mpi
```

The above line will create a new profile directory `$HOME/.ipython/profile_mpi` and some configuration specific files which we can modify to allow use to run MPI-enabled jobs to suit our environment. While not all steps here may be necessary for all configurations, this is currently what has given the correct mpi4py output in the rest of the notebook.

Firstly, we must modify the `c.IPClusterEngines.engine_launcher_class` and `c.IPClusterStart.controller_launcher_class` variables in `$HOME/.ipython/profile_mpi/ipcluster_config.py` around lined 127 and 178 to:
```bash
c.IPClusterEngines.engine_launcher_class = 'MPIEngineSetLauncher'
...
c.IPClusterStart.controller_launcher_class = 'MPIControllerLauncher'
```

Next, we modify the `ipcluster` command (location found with `whcih ipcluster`) to use `libtbx.python` instead of the default `ipython` environment to ensure we have the appropriate paths variables set. For ease of use, we can simply call the following command: 
```bash
sed -i "1 s~^.*$~\#\!$(which libtbx.python)~" $(which ipcluster)
```

This will set up the environment to allow MPI-enabled jobs. We can now start our `ipcluster` environment with:
```bash
ipcluster start -n <CORES> --profile=mpi --engines=MPI
```
where `<CORES>` specifies the number of back-end MPI engines (like ranks) on which to run our jobs. We may now connect our notebook to the cluster backend, and test the functionality of mpi4py. We may also enable the ability to start and stop the cluster profiles within the Jupyterhub environment by running the following command in the terminal:
```bash
ipcluster nbextension enable --user
```
This will enable the IPythonClusters tab, and allow us to specify the number of cores and/or profiles to start.

We must ensure the mpi4py module is built with and run with the same MPI library. The shell environment that enables the Jupyter notebook and the ipycluster backend should allow for mpi4py scripts to run. As a test, ensure that the following code can run in the terminal environment:

```python
from mpi4py import MPI

size = MPI.COMM_WORLD.Get_size()
rank = MPI.COMM_WORLD.Get_rank()
name = MPI.Get_processor_name()

print "Rank %d of %d [%s]."%(rank, size, name)
```
using `mpirun -n 4 libtbx.python mpi_test.py`. If the output shows 4 ranks, next run the following command in the notebook, and the output should be identical (though different order of ranks is possible).

In [2]:
!mpirun -n 4 libtbx.python ./mpi_test.py

Rank 0 of 4 [dials.lbl.gov].
Rank 1 of 4 [dials.lbl.gov].
Rank 2 of 4 [dials.lbl.gov].
Rank 3 of 4 [dials.lbl.gov].


Now, we can tie the MPI backend into the notebook to allow us to call jobs on the cluster backend 

In [3]:
from ipyparallel import Client
c = Client(profile='mpi')

def mpi_test():
    from mpi4py import MPI
    print MPI.COMM_WORLD.size

    size = MPI.COMM_WORLD.Get_size()
    rank = MPI.COMM_WORLD.Get_rank()
    name = MPI.Get_processor_name()    

    return (rank, size, name)
c.ids
rc=c[:]
rc.apply_sync(mpi_test)

[(6, 8, 'dials.lbl.gov'),
 (4, 8, 'dials.lbl.gov'),
 (5, 8, 'dials.lbl.gov'),
 (3, 8, 'dials.lbl.gov'),
 (1, 8, 'dials.lbl.gov'),
 (0, 8, 'dials.lbl.gov'),
 (2, 8, 'dials.lbl.gov'),
 (7, 8, 'dials.lbl.gov')]

We can enable interactive Matplotlib within the notebook environment.

In [4]:
%matplotlib nbagg
import matplotlib.pyplot as plt

We now attempt to import a cctbx module and run a command using this, to ensure our environment is correctly configured. We import the Flex module, create a flex.double array from a python list of floats, then convert back to a list and print the values. If this succeeds, our environment is configured correctly.

In [5]:
from scitbx.array_family import flex
print list(flex.double([1.0,2.0,3.0]))

[1.0, 2.0, 3.0]


We start with defining the location of our desired directories:
- RESULTDIR is the base directory for all our analysis
- OUTDIR is where the scripts and different merge directory will live
- {OUTDIR}/subsel is for storing temporary directories for holding softlinks to the TAR files to merge
- TARDIR is the location of all TAR files
- PHENIXDIR is the location of the Phenix installation
- EXAFELDIR is the location of the exafel_project repo.

In [9]:
RESULTDIR="/net/dials/raid1/mlxd/InDev/feb_sprint/"
OUTDIR=RESULTDIR+'/nested_merging2'
%mkdir -p {OUTDIR}/subsel
%cd {OUTDIR}
TARDIR='/net/dials/raid1/mlxd/TAR/'
PHENIXDIR="/net/cci/mlxd/ml/builds/sept_sprint/myDir/phenix"
EXAFELDIR="/net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging/exafel_project"

/net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2


Next, we take a count of the total number of cores on the system, and set the scripts to use this amount of MPI-ranks when merging. 

In [28]:
import multiprocessing as mp
cores = mp.cpu_count()-1

To best allow for the MPI-enabled process to run, we can examine two methods: 
1. Using shell scripts to generate the required files and merge commands which are called from the notebook 
2. Running the MPI-enabled work entirely from within the notebook.

We will examine option 1. initially, and see if this fits out needs.

Firstly, we create the command-scripts to compute the nested merge jobs. We can begin with a templated file with sections to replace with the desired values for each merge job. We create a bash array which maintains a list of all the files matching the specific TAR run numbers required for the merge (eg [95], [95,96], [95,96,97], etc.). We then patch the submission script, replacing the `<templated>` regions with the required values.

In [29]:
MERGE='''
cd <OUTDIR>;

TMPDIR=$(mktemp -d);
if [ -z "${TMPDIR}" ]
then
  echo 'Failed to create temporary directory. Exiting.';
  exit -1;
fi

DATADIR=<OUTDIR>/subsel/$(basename ${TMPDIR});
ln -sf ${TMPDIR} ${DATADIR};
for ii in $(ls <TARDIR>/<glob_template>);
do
  ln -sf ${ii} ${DATADIR}
done;
trap "{ rm -rf ${TMPDIR}; rm <OUTDIR>/subsel/$(basename ${TMPDIR}); }" ERR EXIT
export TARDATA=${DATADIR}/*.tar;
cp /net/dials/raid1/mlxd/InDev/test/refModel/4ngz* <OUTDIR>;
export MERGE_ROOT=<OUTDIR>;
export TAG=1n_merge_<tag_template>;
export MULTINODE=True;
mkdir -p ${MERGE_ROOT}/${TAG};

source ${CONDA_PREFIX}/../../bin/activate myEnv
echo "START RANK=0 TIME=" $(date +%s);
/net/dials/raid1/mlxd/InDev/builds/openmpi-3.0.0/bin/mpiexec -np <CORES> <EXAFELDIR>/137-nested_merge/merge_local.sh;
echo "STOP RANK=0 TIME=" $(date +%s);

export EXAFEL_DIR=<EXAFELDIR>
export PHENIX_ROOT=<PHENIXDIR>
export MULTINODE=False;
<EXAFELDIR>/137-nested_merge/merge_local.sh;
'''
MERGE = MERGE.replace('<OUTDIR>',OUTDIR)\
.replace('<TARDIR>',TARDIR)\
.replace('<CORES>', str(cores))\
.replace('<PHENIXDIR>', PHENIXDIR)\
.replace('<EXAFELDIR>',EXAFELDIR)
MERGE_FILE = open("MERGE_FILE.sh", "w")
MERGE_FILE.write(MERGE)
MERGE_FILE.close()

The above file explicitly sets up directories containing softlinks to the files for each nested merge step, and runs these using the specified commands in `exafel_project/137-nested_merge/merge_local.sh`. The resulting directory containing the softlinks is removed upon exit of the script. We now generate the templated files for each merging job, and subsequently run these providing the location of the `<OUTDIR>` and the `<exafel_project>` directory as arguments.

In [30]:
%%bash
shopt -s extglob
export TARDIR=$TARDIR #Pass in the directory with the tar files:   eg  /my/scratch/dir/TAR_95-114
export OUTDIR=$OUTDIR #Pass in the directory for burst-buffer data to be staged out:   /my/scratch/dir/bb_out
RUNARRAY=() #Array to hold the structure of the files to be processed

#Iterate over the given runs and generate the TAR globs
echo "Generating expanded globs for TAR file paths"
for ii in $(seq -w 95 114); do
  RUNARRAY+=($ii)
  str=""
  for jj in ${RUNARRAY[@]}; do
    str+=$jj,
  done
  str=$(echo $str | sed s'/.$//')
  if [ "${#RUNARRAY[@]}" == "1" ]; then
    g=$(eval "echo \"r0${str}*.tar\" ")
  else
    g=$(eval "echo \"r0{${str}}*.tar\" ") 
  fi  
  echo $g
  
  #Create a submission script with the appropriate arguments
  cat ./MERGE_FILE.sh | sed "s~<tag_template>~r0${ii}~g; s~<glob_template>~${g}~g; s~<tar_template>~${TARDIR}~g; s~<data_out_template>~${OUTDIR}~g" > merge_r0${ii}.sh
  chmod +x merge_r0${ii}.sh
done

Generating expanded globs for TAR file paths
r0095*.tar
r0{095,096}*.tar
r0{095,096,097}*.tar
r0{095,096,097,098}*.tar
r0{095,096,097,098,099}*.tar
r0{095,096,097,098,099,100}*.tar
r0{095,096,097,098,099,100,101}*.tar
r0{095,096,097,098,099,100,101,102}*.tar
r0{095,096,097,098,099,100,101,102,103}*.tar
r0{095,096,097,098,099,100,101,102,103,104}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110,111}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110,111,112}*.tar
r0{095,096,097,098,099,100,101,102,103,104,105,106,107,108,109,110,111,112,113}*.tar
r0{095,096,097,098,099,100

To run the merge job for run95 using the generated bash scripts, we run the following command.

In [21]:
! ./merge_r0095.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/

START RANK=0 TIME= 1520648393
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.TPHQO1iFqS/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0095 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scaling.mtz_file=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz scaling.mtz_column_F=f(+) min_corr=-1.0 unit_cell_length_tolerance=0.0065 raw_data.errors_from_sample_residuals=False raw_data.sdfac_refine=True raw_data.error_models.sdfac_refine.random_seed=42 cell_rejection.unit_cell=79.0,79.0,38.1,90,90,90 cell_rejection.space_group=P43212 output.prefix=1n_merge_r0095
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.TPHQO1iFqS/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0095 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scali

The following parameters have been modified:

targlob = "/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.TPHQO1iFqS/*.tar"
model = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb
d_min = 2.0
pixel_size = 0.11
min_corr = -1.0
unit_cell_length_tolerance = 0.0065
nproc = 1
raw_data {
  sdfac_refine = True
  error_models {
    sdfac_refine {
      random_seed = 42
    }
  }
}
output {
  prefix = 1n_merge_r0095
}
scaling {
  mtz_file = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz
  mtz_column_F = f(+)
  report_ML = True
}
postrefinement {
  enable = True
}
cell_rejection {
  unit_cell = 79.0,79.0,38.1,90,90,90
  space_group = P43212
}
backend = *FS MySQL SQLite Flex
mysql {
  runtag = 1n_merge_r0095
}

I model
Number of scatterers: 1164
At special positions: 0
Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
Space group: P 43 21 2 (No. 96)
Miller array info: None
Observation type: None
Type of data: double, size=15080
Type of sigmas: do

  12  1.8769 -  1.8235 [ 2/1631]        11.9       0.8
Step 5. Frame by frame resolution filter
Total obs 64 Choose n bins = 6

 Bin  Resolution Range  Compl.         <I>     <I/sig(I)>
   1 11.1629 -  3.2898 [20/3288]      1553.2      29.0
   2  3.2898 -  2.6224 [15/3265]       545.4      15.7
   3  2.6224 -  2.2942 [14/3285]       195.1       9.8
   4  2.2942 -  2.0859 [ 6/3294]        31.7       2.5
   5  2.0859 -  1.9372 [ 6/3280]        51.0       3.0
   6  1.9372 -  1.8235 [ 3/3262]        25.1       2.1
New resolution filter at    1.82 /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.TPHQO1iFqS/r0095_int-0-0413.pickle.tar;member00000;timestampint-0-20140615213940085.pickle
N acceptable bins 6
Old n_obs: 64, new n_obs: 64
Step 6.  Match to reference intensities, filter by correlation, filter out negative intensities.
Old correlation is 0.582177628003
functional 111714159.515
rms   1376.031 G:  0.0072587 B:  0.0000000 RS:  0.0001101   0.000 deg   0.000 deg
rms   

--------------------------------------------------------------------------------
Step 2.  Load pickle file into dictionary obj and filter on lattice & cell with h,k,l
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.TPHQO1iFqS/r0095_int-0-0022.pickle.tar;member00000;timestampint-0-20140615213927890.pickle

P 4/m m m
(79.2633, 79.2633, 38.2048, 90, 90, 90)
Integrated data:
  Miller array info: None
  Observation type: xray.intensity
  Type of data: double, size=81
  Type of sigmas: double, size=81
  Number of Miller indices: 81
  Anomalous flag: None
  Unit cell: (79.2633, 79.2633, 38.2048, 90, 90, 90)
  Space group: P 4/m m m (No. 123)
mean diff is 0.235498660628 range 0.0117811090097 0.433285169736
Step 3. Correct for polarization.
Step 4. Filter on global resolution and map to asu
Data in reference setting:

 Bin  Resolution Range  Compl.         <I>     <I/sig(I)>
   1 11.9809 -  4.1769 [ 8/1577]      3287.1      43.6
   2  4.1769 -  3.3390 [ 9/1573]      8560.5   

--------------------------------------------------------------------------------
Step 2.  Load pickle file into dictionary obj and filter on lattice & cell with h,k,l
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.TPHQO1iFqS/r0095_int-0-0349.pickle.tar;member00000;timestampint-0-20140615213943485.pickle

P 4/m m m
(79.119, 79.119, 38.1142, 90, 90, 90)
Integrated data:
  Miller array info: None
  Observation type: xray.intensity
  Type of data: double, size=56
  Type of sigmas: double, size=56
  Number of Miller indices: 56
  Anomalous flag: None
  Unit cell: (79.119, 79.119, 38.1142, 90, 90, 90)
  Space group: P 4/m m m (No. 123)
mean diff is 0.214578091956 range 0.0528501847728 0.395071191162
Step 3. Correct for polarization.
Step 4. Filter on global resolution and map to asu
Data in reference setting:

 Bin  Resolution Range  Compl.         <I>     <I/sig(I)>
   1 5.4688 - 3.8865 [9/1312]     11537.0      90.2
   2 3.8865 - 3.2950 [7/1304]      7743.9      74.8
  

...

48.08 52.67   4.60  0.002   0.4    0.0   0.0   0.0    0  0.125  6.302  0.0093
47.29 52.40   5.11  0.004   0.5    0.5   0.0   0.0    0  0.250  6.285  0.0109
46.13 52.33   6.20  0.006   0.7    2.5   0.0   0.0    0  0.500  6.258  0.0168
44.99 52.57   7.59  0.009   1.1    6.1   0.0   0.0    0  1.000  6.233  0.0274
43.44 53.48  10.04  0.013   1.6   14.8   0.8   0.0    0  2.000  6.198  0.0524
42.83 54.13  11.30  0.018   2.0   24.5   3.1   0.0    0  3.000  6.176  0.0799
42.27 54.33  12.06  0.022   2.3   33.6   3.1   1.9    0  4.000  6.156  0.1099
41.80 54.31  12.52  0.026   2.5   40.2   3.1   1.9    0  5.000  6.142  0.1284
41.36 54.34  12.99  0.031   2.8   42.3   3.1   2.9    0  6.000  6.130  0.1560
41.05 54.51  13.46  0.033   3.1   50.9   3.1   2.9    1  7.000  6.119  0.2004
40.81 54.56  13.75  0.036   3.3   57.1   3.1   4.8    3  8.000  6.108  0.2148
40.49 55.03  14.55  0.040   3.5   60.6   3.1   4.8    4  9.000  6.099  0.2487
40.30 55.17  14.87  0.043   3.7   61.1   4.7   5.7    5 10.000  


                         ----------X-ray data----------                        

|--(resolution: 2.00 - 25.49 A, n_refl.=2152 (all), 7.62  % free)-------------|
|                                                                             |
| r_work= 0.4819 r_free= 0.5269 coordinate error (max.-lik. estimate): 0.61 A |
|                                                                             |
| normalized target function (ml) (work): 6.302844                            |
| target function (ml) not normalized (work): 12530.054376                    |
| target function (ml) not normalized (free): 1024.547602                     |
|-----------------------------------------------------------------------------|

|-----------------------------------------------------------------------------|
| Bin     Resolution   Compl.  No. Refl.    R-factors          Targets        |
|number     range              work test   work   test        work        test|
|  1: 25.4898 -  2.0007 0.14   1988  


============================== Collecting inputs ==============================


                   ----------Processing X-ray data----------                   

I-obs:
  /net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2/1n_merge_r0095/1n_merge_r0095.mtz:Iobs(+),SIGIobs(+),Iobs(-),SIGIobs(-)
Miller array info: /net/dials/raid1/mlxd/InDev/feb_sprint/nested_merging2/1n_merge_r0095/1n_merge_r0095.mtz:Iobs(+),SIGIobs(+),Iobs(-),SIGIobs(-)
Observation type: xray.intensity
Type of data: double, size=2295
Type of sigmas: double, size=2295
Number of Miller indices: 2295
Anomalous flag: True
Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
Space group: P 43 21 2 (No. 96)
Systematic absences: 0
Centric reflections: 278
Resolution range: 25.4878 2.00067
Completeness in resolution range: 0.153337
Completeness with d_max=infinity: 0.153266
Anomalous completeness in resolution range: 0.0269626
Bijvoet pairs: 181
Lone Bijvoet mates: 1655
Mean anomalous difference: 0.7760
Wavelength: 1.3853


  

(-11, -2, -16)    63461.477      334110.438    30171.216
(-32, -9, -6)    132993.422      1071457.625    31614.456
(37, 4, 0)    52837.633      972054.688    21804.937
(-35, -3, -6)    16263.574      169479.188    20940.654
(-36, -3, -3)    72280.094      914388.438    24700.954
(32, 15, 7)    23470.793      436097.500    21751.396
(-16, -1, -16)    18770.402      129551.742    19834.648
(-29, -16, -9)    10105.749      197811.391    20817.468
-----------------------------------------------------------------
Intensities converted to amplitudes for use in refinement.

Number of F-obs in resolution range:                   2171
Number of F-obs<0 (these reflections will be rejected): 0
Number of F-obs=0 (these reflections will be used in refinement): 0
Refinement resolution range: d_max =  25.4878
                             d_min =   2.0007


Fobs statistics after all cutoffs applied:

Miller array info: None
Observation type: xray.amplitude
Type of data: double, size=2014
Type of sigma

      100.55 -   107.24: 49
      107.24 -   113.92: 2210
      113.92 -   120.60: 709
      120.60 -   127.28: 565
      127.28 -   133.97: 15
  Bond angle restraints: 3548
  Sorted by residual:
  angle pdb=" CA  SER A  36 "
        pdb=" C   SER A  36 "
        pdb=" N   ASN A  37 "
      ideal   model   delta    sigma   weight residual
     116.20  119.47   -3.27 2.00e+00 2.50e-01 2.67e+00
  angle pdb=" CA  ARG A 114 "
        pdb=" C   ARG A 114 "
        pdb=" N   CYS A 115 "
      ideal   model   delta    sigma   weight residual
     116.20  119.28   -3.08 2.00e+00 2.50e-01 2.37e+00
  angle pdb=" CA  TRP A  63 "
        pdb=" C   TRP A  63 "
        pdb=" N   CYS A  64 "
      ideal   model   delta    sigma   weight residual
     116.20  119.19   -2.99 2.00e+00 2.50e-01 2.23e+00
  angle pdb=" CA  ARG A  68 "
        pdb=" C   ARG A  68 "
        pdb=" N   THR A  69 "
      ideal   model   delta    sigma   weight residual
     116.20  119.09   -2.89 2.00e+00 2.50e-01 2.09e+00
  an

We can now parse the output directory for information on the resulting merge job. In this instance, we simply look for the number of frames used, and the resulting anomalous peak height value. Though, we can opt to look for additional parameters quite easily.

In [26]:
%%bash
for ii in $(find $PWD -type f -iname "1n_merge_*.log" | grep -v mark0 | grep -v graphs | grep -v peak | grep -v 001);
do
  echo $(basename $ii);
  sed '9q;d' $ii;
done
for ii in $(find $PWD -type f -iname "*peak*log");
do
  echo $(basename $ii)
  str=$(tail -n 1 $ii)
  if [[ "$str" = *"sigma"* ]]; then
      echo $str
  else
      echo "Unable to calculate anom. peak height."
  fi
done

1n_merge_r0095.log
  38 of 38 integration files were accepted
1n_merge_r0099.log
  666 of 997 integration files were accepted
1n_merge_r0114.log
  134773 of 142194 integration files were accepted
1n_merge_r0095_peakht.log
Unable to calculate anom. peak height.
1n_merge_r0099_peakht.log
pdb="YB YB A 203 " : 2.57 sigma
1n_merge_r0114_peakht.log
pdb="YB YB A 203 " : 36.04 sigma


As we can see, using very little data gives us a poor result for the anom. peak height (in this case, no result). We can run one of the other nested merge scripts with more data to allow us to acquire a result. We begin by adding in runs 96 to 99 to the job using:

In [23]:
! ./merge_r0099.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/

START RANK=0 TIME= 1520648679
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0099 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scaling.mtz_file=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz scaling.mtz_column_F=f(+) min_corr=-1.0 unit_cell_length_tolerance=0.0065 raw_data.errors_from_sample_residuals=False raw_data.sdfac_refine=True raw_data.error_models.sdfac_refine.random_seed=42 cell_rejection.unit_cell=79.0,79.0,38.1,90,90,90 cell_rejection.space_group=P43212 output.prefix=1n_merge_r0099
d_min=2.0 targlob="/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/*.tar" model=/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb backend=FS mysql.runtag=1n_merge_r0099 scaling.report_ML=True pixel_size=0.11 nproc=1 postrefinement.enable=True scali

The following parameters have been modified:

targlob = "/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/*.tar"
model = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.pdb
d_min = 2.0
pixel_size = 0.11
min_corr = -1.0
unit_cell_length_tolerance = 0.0065
nproc = 1
raw_data {
  sdfac_refine = True
  error_models {
    sdfac_refine {
      random_seed = 42
    }
  }
}
output {
  prefix = 1n_merge_r0099
}
scaling {
  mtz_file = /net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/4ngz.mtz
  mtz_column_F = f(+)
  report_ML = True
}
postrefinement {
  enable = True
}
cell_rejection {
  unit_cell = 79.0,79.0,38.1,90,90,90
  space_group = P43212
}
backend = *FS MySQL SQLite Flex
mysql {
  runtag = 1n_merge_r0099
}

I model
Number of scatterers: 1164
At special positions: 0
Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
Space group: P 43 21 2 (No. 96)
Miller array info: None
Observation type: None
Type of data: double, size=15080
Type of sigmas: do

/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0207.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0208.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0209.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0211.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0212.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0215.pickle.tar 3
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0216.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0217.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0218.pickle.tar 1
/net/dials/raid1/mlxd/InDev/

/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0395.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0397.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0399.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0400.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0402.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0406.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0407.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0408.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0096_int-0-0412.pickle.tar 1
/net/dials/raid1/mlxd/InDev/

/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0075.pickle.tar 2
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0077.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0079.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0080.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0081.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0082.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0084.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0085.pickle.tar 1
/net/dials/raid1/mlxd/InDev/feb_sprint//nested_merging2/subsel/tmp.x39c27ta9F/r0097_int-0-0087.pickle.tar 1
/net/dials/raid1/mlxd/InDev/

...

(-25, -5, -4)    185347.203      670913.000    152379.207
(25, 10, 1)    290815.938      631133.000    132977.619
(26, 4, 3)    133686.891      615639.312    140822.299
(13, 12, 10)    1115750.750      2772810.500    171907.526
(-21, -14, -5)    1105597.250      1148734.625    191605.316
(-24, -13, -1)    528749.125      1046429.375    191091.012
(24, 13, 2)    296580.500      991111.375    174417.775
(-24, -13, -2)    531328.688      1096433.500    174417.775
(26, 7, 3)    705755.812      892777.938    165406.831
(-26, -7, -3)    595832.688      1180302.750    165406.831
(-26, -8, -1)    359086.469      1277784.500    176433.406
(22, 17, 0)    1588345.250      2318858.250    139256.371
(11, 4, 12)    245056.344      1099420.000    109967.796
(-18, -1, -10)    955861.000      856333.562    129730.740
(19, 8, 9)    220699.719      508805.219    105020.749
(20, 10, 8)    190047.828      541845.250    107007.360
(-20, -10, -8)    233727.188      526822.625    107007.360
(20, 19, 2)    232

(-15, -12, -13)    197770.719      454295.344    59241.558
(17, 14, 12)    87438.703      341017.812    61608.595
(-17, -14, -12)    171275.719      366700.469    61608.595
(-24, -14, -9)    97692.750      470042.875    63767.242
(24, 20, 6)    214139.266      924825.250    64596.063
(24, 21, 5)    63844.461      249791.406    58484.126
(-24, -21, -5)    257307.531      374273.281    58484.126
(25, 17, 7)    141753.266      345649.406    62179.426
(25, 20, 5)    87875.258      315594.562    64184.535
(-25, -20, -5)    146928.969      438149.344    64184.535
(26, 17, 6)    70778.688      263295.812    57781.570
(-27, -18, -4)    134382.969      412421.812    58340.402
(27, 19, 3)    91023.805      436990.719    59115.871
(-27, -19, -3)    173055.938      407639.531    59115.871
(28, 8, 8)    215054.828      305103.438    63323.780
(-29, -1, -8)    130888.984      424464.344    59047.280
(-30, -1, -7)    129211.789      343987.125    59191.361
(-30, -3, -7)    243756.938      483437.938 

(-30, -22, -3)    41088.734      174922.516    32401.774
(9, 8, 17)    76440.469      218793.469    32942.898
(17, 12, 15)    58320.660      280132.500    32870.338
(-26, -1, -13)    221789.125      420455.406    32291.805
(-35, -1, -7)    75016.367      286141.938    32850.253
(20, 13, 14)    51512.566      178728.234    34172.464
(-26, -3, -13)    56598.477      167542.078    32842.154
(-31, -6, -10)    40043.852      157763.328    32971.359
(-26, -12, -12)    52493.512      203837.297    37369.992
(31, 20, 5)    141200.422      532737.875    37352.952
(34, 17, 2)    66193.570      257439.672    36854.237
(36, 11, 3)    210368.172      398954.500    35474.283
(28, 20, 8)    62044.773      193385.453    37357.414
(34, 5, 8)    54396.719      252332.125    37368.471
(36, 1, 6)    51929.445      220042.375    35904.107
(-26, -25, -6)    136892.328      318606.844    36913.456
(-30, -5, -11)    65432.926      257512.297    37365.081
(-32, -12, -8)    90085.523      192171.125    35196.54

  Number of scatterers: 2004
  At special positions: 1
  Unit cell: (78.589, 78.589, 37.017, 90, 90, 90)
  Space group: P 43 21 2 (No. 96)
  Number of sites at special positions: 1
    Minimum distance between symmetrically equivalent sites: 0.5
    Label                   Mult   Shift    Fractional coordinates
    pdb=" O   HOH S  10 "     4    0.000 (  0.1831   0.1831   0.0000) original
                          site sym 2     (  0.1831   0.1831   0.0000) exact
                                          1/2*x+1/2*y,1/2*x+1/2*y,0
  Number of scattering types: 8
    Type  Number    sf(0)
     Yb3+     1     66.98
     Cl1-     1     17.99
     S       10     16.00
     Na1+     1     10.00
     O      226      8.00
     N      193      7.00
     C      613      6.00
     H      959      1.00
    sf(0) = scattering factor at diffraction angle 0.

  Number of disulfides: simple=4, symmetry=0
    Simple disulfide: pdb=" SG  CYS A   6 " - pdb=" SG  CYS A 127 " distance=2.00
    Simple disul


=============================== Model properties ==============================

  Overall:
    Number of atoms = 1045  (anisotropic = 1)
    B_iso: mean =  19.4  max =  72.2  min =   4.4
    Occupancy: mean = 1.00  max = 1.00  min = 0.54
    10 total B-factor or occupancy problem(s) detected
  Macromolecules:
    Number of atoms = 1001  (anisotropic = 0)
    B_iso: mean =  19.4  max =  72.2  min =   6.0
    9 total B-factor or occupancy problem(s) detected
  Ligands:
    Number of atoms = 3  (anisotropic = 1)
    B_iso: mean =  28.6  max =  49.2  min =  17.8
    Occupancy: mean = 0.85  max = 1.00  min = 0.54
    1 total B-factor or occupancy problem(s) detected
  Waters:
    Number of atoms = 41  (anisotropic = 0)
    B_iso: mean =  17.9  max =  41.4  min =   4.4
  (Hydrogen atoms not included in overall counts.)

============================ Molprobity validation ============================


=================================== Summary ===================================

  RMS(bon

In [34]:
%%bash
for ii in $(find $PWD -type f -iname "1n_merge_*.log" | grep -v mark0 | grep -v graphs | grep -v peak | grep -v 001);
do
  echo $(basename $ii);
  sed '9q;d' $ii;
done
for ii in $(find $PWD -type f -iname "*peak*log");
do
  echo $(basename $ii)
  str=$(tail -n 1 $ii)
  if [[ "$str" = *"sigma"* ]]; then
      echo $str
  else
      echo "Unable to calculate anom. peak height."
  fi
done

1n_merge_r0095.log
  38 of 38 integration files were accepted
1n_merge_r0099.log
  666 of 997 integration files were accepted
1n_merge_r0114.log
  134793 of 142194 integration files were accepted
1n_merge_r0095_peakht.log
Unable to calculate anom. peak height.
1n_merge_r0099_peakht.log
pdb="YB YB A 203 " : 2.57 sigma
1n_merge_r0114_peakht.log
pdb="YB YB A 203 " : 36.90 sigma


We now have enough data for a value to be calculated (albeit a very small one). Performing the merging with higher runs will allow the number to increase even further. Using this method we are running the merging jobs interactively. It may make more sense to run the jobs asynchronously using the IPyCluster backend we mentioned earlier. This way, we get an immediate return from the job submission, and can easily work in the notebook wihile the jobs are running in the background. 

Otherwise, we can simply call the previous submission script using the entire data set. As this job may take a long time, it may be worth sending the calling process into the background, so that we may manipulate other cells in the notebook.


In [92]:
%%script bash --bg 
./merge_r0114.sh {OUTDIR} \
    {OUTDIR}/exafel_project/137-nested_merge/ &> ./background_output.log

Starting job # 2 in a separate thread.


In [ ]:
!tail -f ./background_output.log

Now we would like to view the results of the merging job. We can use Pandas' DataFrame object to display the resulting table data. Here we will examine the nested merge output using all data (runs 95 to 114).

In [110]:
from exafel_project.mlxd.utils import pd_table as pdt
tb = pdt.pd_table(OUTDIR,'1n_merge_r0114')

['CRYST1', '78.589', '78.589', '37.017', '90.00', '90.00', '90.00', 'P', '43', '21', '2']
['REMARK', '3', '9', '2.0801', '-', '2.0000', '1.00', '1515', '141', '0.2286', '0.2401', '0.875', '0.830']


Jupyter notebooks nicely format pandas DataFrame objects, so we can view the resulting tables 1 and 2 in their own cells as:

In [108]:
tb.t1

Anomalous peak height  Bond angles  Bond lengths  CC*        CC1/2 CCano  \
0                   36.9        0.557         0.003  N/A  99.6 (94.5)   N/A   

        CCiso  Clashscore   Completeness  Favored  ...   \
0  65.2 (9.9)        1.53  100.0 (100.0)    98.43  ...    

           Rwork / Rfree  Space group Water Wilson B factor             a  \
0  17.5/19.7 (22.9/24.0)    P 43 21 2    80           13.08  78.96+/-0.11   

   alpha             b  beta             c gamma  
0   90.0  78.96+/-0.11  90.0  38.12+/-0.06  90.0  

[1 rows x 31 columns]

In [109]:
tb.t2

<I/sigI>  <Multiplicity>  CC1/2  CCiso  Completeness  No. Lattices  \
0    30.371         1363.37   99.5   69.6         99.67        134512   
1    23.768          808.93   99.5   48.0        100.00        130990   
2    21.224          656.22   99.3   38.1        100.00        127887   
3    18.932          538.13   99.2   31.4        100.00        125279   
4    17.845          489.71   99.2   19.4        100.00        123607   
5    17.518          482.29   98.8   11.2        100.00        123008   
6    16.376          426.40   99.0   13.8        100.00        120551   
7    14.206          330.04   98.0   18.1        100.00        115801   
8    11.987          237.71   97.1    7.1        100.00        106287   
9     9.882          161.69   94.5    9.9        100.00         94431   

   No. Measurements No. Unique reflections Resolution High Resolution Low  \
0           2055963                   1503            4.31            inf   
1           1207737                   1493            3.42           4.31   
2            981049                   1495            2.99           3.42   
3            808264                   1502            2.71           2.99   
4            735539                   1502            2.52           2.71   
5            721026                   1495            2.37           2.52   
6            634051                   1487            2.25           2.37   
7            500676                   1517            2.15           2.25   
8            350378                   1474            2.07           2.15   
9            243983                   1509            2.00           2.07   

   Rsplit  
0     4.1  
1     3.9  
2     4.5  
3     5.0  
4     4.9  
5     5.3  
6     5.7  
7     6.8  
8     8.5  
9    10.9

##################################

[TBC - These cells are in development, and may fail outright] 

We can call the `dev_cluster_two_merge.py` script by first importing it and then providing the Phil params within the notebook (non-shell) environment. 

In [33]:
effective_params="d_min=2.0 \
targlob=\"${TARDATA}\" \
model=${MERGE_ROOT}/4ngz.pdb \
backend=FS \
mysql.runtag=${trial} \
scaling.report_ML=True \
pixel_size=0.11 \
nproc=1 \
postrefinement.enable=True \
scaling.mtz_file=${MERGE_ROOT}/4ngz.mtz \
scaling.mtz_column_F=f(+) \
min_corr=-1.0 \
unit_cell_length_tolerance=0.0065 \
raw_data.errors_from_sample_residuals=False \
raw_data.sdfac_refine=True \
raw_data.error_models.sdfac_refine.random_seed=42 \
cell_rejection.unit_cell=78.95,78.95,38.12,90,90,90 \
cell_rejection.space_group=P43212 \
output.prefix=${trial}"

In [17]:
def run_merge():
    from xfel.merging.command_line import dev_mpi_cluster_two_merge as c2m
    from mpi4py import MPI
    comm = MPI.COMM_WORLD
    rank = comm.Get_rank()

    script = c2m.Script(c2m.scaling_manager_mpi)
    result = script.run(comm=comm,timing=False)
    if rank == 0:
      script.show_plot(result)
    print "DONE"

In [14]:
c = Client(profile='mpi')
rc=c[:]
rc.apply_async(run_merge)

<AsyncResult: run_merge>